 * [DeepSeek-R1-Distill-Qwen-7B](#DeepSeek-R1-Distill-Qwen-7B)
 * [2003](#2003)
 * [1998](#1998)
 * [1999](#1999)
 * [2000](#2000)
 * [2020](#2020)
 * [2004](#2004)
 * [2008](#2008)
 * [2009](#2009)
 * [2001](#2001)
 * [2006](#2006)
 * [2010](#2010)
 * [2002](#2002)
 * [2005](#2005)
 * [2015](#2015)
 * [2019](#2019)
 * [2011](#2011)
 * [2012](#2012)
 * [2017](#2017)
 * [2007](#2007)
* [2013](#2013)
* [2014](#2014)
* [2016](#2016)
* [2018](#2018)

# DeepSeek-R1-Distill-Qwen-7B

In [1]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2024 NVIDIA Corporation
Built on Thu_Jun__6_02:18:23_PDT_2024
Cuda compilation tools, release 12.5, V12.5.82
Build cuda_12.5.r12.5/compiler.34385749_0


In [2]:
!nvidia-smi

Sun Jun 29 12:15:59 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 560.35.03              Driver Version: 560.35.03      CUDA Version: 12.6     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   41C    P8              9W /   70W |       1MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [3]:
import torch
import pandas as pd
import time
import numpy as np
import threading
import subprocess
import pynvml
import os
import shutil
import re
import sys
import zipfile
import gc # For garbage collection and clearing CUDA cache

In [4]:
print(torch.__version__)          # e.g. '2.1.0'
print(torch.cuda.is_available())  # should be True on Kaggle GPU

2.6.0+cu124
True


In [5]:
!pip install hf_xet

In [6]:
from transformers import AutoTokenizer,AutoConfig, LlamaTokenizer , AutoModelForCausalLM, BitsAndBytesConfig
from huggingface_hub import snapshot_download
from sentence_transformers import SentenceTransformer, util
from nltk.translate.bleu_score import sentence_bleu
from tqdm import tqdm
from accelerate import infer_auto_device_map, init_empty_weights
from IPython.display import FileLink
from pathlib import Path

2025-06-29 12:16:16.777963: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751199376.977277      35 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751199377.038647      35 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [7]:
print("CUDA available:", torch.cuda.is_available())  # Should be True
print("Number of GPUs:", torch.cuda.device_count())   # Should be 2|

CUDA available: True
Number of GPUs: 2


In [8]:
def create_master_zip_flat(year):
    year_str = str(year)
    master_zip_path = f"/kaggle/working/{year_str}_{model_small}_ALL_PARAPHRASED.zip"
    base_dir = os.path.join("/kaggle/working", year_str)

    with zipfile.ZipFile(master_zip_path, 'w') as master_zip:
        for root, dirs, files in os.walk(base_dir):
            for file in files:
                if file.startswith("paraphrase_") and file.endswith(".txt"):
                    full_path = os.path.join(root, file)

                    # Extract CIK from the path (immediately after the year folder)
                    rel_parts = os.path.relpath(full_path, base_dir).split(os.sep)
                    if len(rel_parts) >= 2:
                        cik = rel_parts[0]
                        arcname = os.path.join(cik, file)
                        master_zip.write(full_path, arcname=arcname)

    print(f"✅ Master ZIP created with flat structure: {master_zip_path}")
    return master_zip_path

In [9]:
# --- Paraphrase instruction: Emphasize start immediately and end with **** ---
paraphrase_instruction = '''


Your task is to paraphrase the above "Original text" in a way that preserves its full meaning while making the wording, 
sentence structure, and phrasing as different as possible. Do not merely replace words—change the overall flow and expression.

⚠️ VERY IMPORTANT: You must present your final output using the following EXACT structure, without deviation:

Final Paraphrased:
paraphrased text
^^^^

At any cost, provide only the paraphrased version of the "Original text" strictly between the markers 
Final Paraphrased: and ^^^^. Do not include any explanations, reasoning, thoughts, or commentary 
inside these markers.
So, At any cost, only the paraphrased version of the "Original text" will be inside those markers!

'''
model_small='DEEPSEEK'
model_full='deepseek-qwen-7b'

# 2003

In [ ]:
year=2003

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 1998

In [ ]:
year=1998

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            # Rule 1: Last "Final Paraphrase:" to "****" or end of string
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 1999

In [ ]:
year=1999

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

    
        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)

            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)

            if match:
                extracted_part = match.group(1).strip()
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2000

In [ ]:
year=2000

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

    
        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)

            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)

            if match:
                extracted_part = match.group(1).strip()
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

['811596', '1039780', '887356', '1092657', '316236', '1037067', '888918', '891285', '1005015', '924632', '46601', '764960', '1061583', '945771', '1128709', '922812', '929994', '101063', '1020620', '1047368', '79326', '908797', '795662', '1069602', '95585', '1095827', '829218', '1097523', '1043310', '315136', '73902', '225569', '1061322', '1024401', '1017648', '801351', '830141', '884318', '896265', '11860', '1098341', '1065458', '1047021', '76744', '850660', '1065869', '940716', '937971', '832922', '922978', '1028965', '1052245', '934852', '1052163', '1062515', '1038363', '946323', '757011', '919943', '73093', '1055468', '870213', '46012', '946392', '1013740', '1065633', '1066138', '70578', '947268', '1043769', '913364', '925928', '1054588', '1056312', '731190', '831327', '1054422', '918275', '927417', '1076732', '1017522']

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2020

In [ ]:
year=2020

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2004

In [ ]:
year=2004

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2008

In [ ]:
year=2008

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2009

In [ ]:
year=2009

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2001

In [ ]:
year=2001

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2006

In [ ]:
year=2006

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2010

In [ ]:
year=2010


In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2002

In [ ]:
year=2002

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2005

In [ ]:
year=2005

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2015

In [ ]:
year=2015

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path)[17:]:
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2019

In [ ]:
year=2019

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2011

In [ ]:
year=2011

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2012

In [ ]:
year=2012

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2017

In [ ]:
year=2017

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2007

In [ ]:
year=2007

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2013

In [ ]:
year=2013

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [ ]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

In [ ]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2014

In [10]:
year=2014

The history saving thread hit an unexpected error (OperationalError('attempt to write a readonly database')).History will not be written to the database.


In [11]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['351817', '1422105', '1335190', '837173', '1159154', '1301063', '1568832', '805305', '1560443', '1421182', '1489137', '1385544', '1330849', '1548691', '1336545', '1037676', '1594590', '1553588', '38079']
---------------------------
351817
----------------------------
Report of Independent Registered Public Accounting Firm  The Board of Directors and Stockholders of Swift Energy Company     We have audited the accompanying consolidated balance sheets of Swift Energy Company and subsidiaries (the Company) as of December 31, 2014 and 2013, and the related consolidated statements of operations, comprehensive income, stockholders' equity and cash flows for each of the three years in the period ended December 31, 2014. These financial statements are the responsibility of the Company's management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight

In [12]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


Python garbage collector run.
CUDA cache emptied.
CUDA memory allocated after clearing: 0.00 GB
CUDA memory reserved after clearing: 0.00 GB
--------------------------------------------------
Ready to load a new model or continue with other operations.


In [13]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [14]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [15]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [16]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [17]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

In [18]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [19]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [20]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 0%/6117MB | GPU1: 0%/9429MB


📄 Processing CIK: 351817
----------------------------------------------



CIK NUMBER: 351817



Original AUDIT OPTINION: 
Report of Independent Registered Public Accounting Firm  The Board of Directors and Stockholders of Swift Energy Company     We have audited the accompanying consolidated balance sheets of Swift Energy Company and subsidiaries (the Company) as of December 31, 2014 and 2013, and the related consolidated statements of operations, comprehensive income, stockholders' equity and cash flows for each of the three years in the period ended December 31, 2014. These financial statements are the responsibility of the Company's management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reasonable assurance about whether the financial sta

GPU Utilization:   0%|          | 0% , GPU0: 37%/6265MB | GPU1: 64%/9607MB

GPU Utilization:   0%|          | 0% , GPU0: 37%/6265MB | GPU1: 64%/9607MB

GPU Utilization:   0%|          | 0% , GPU0: 38%/6265MB | GPU1: 59%/9607MB

...

GPU Utilization:   0%|          | 0% , GPU0: 28%/6527MB | GPU1: 60%/9993MB

GPU Utilization:   0%|          | 0% , GPU0: 39%/6527MB | GPU1: 69%/9993MB

GPU Utilization:   0%|          | 0% , GPU0: 28%/6527MB | GPU1: 58%/9993MB

--- RAW LLM Output for Attempt 6 ---
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM   To the Board of Directors and Shareholders of   Sabine Oil & Gas Corporation   Houston, Texas   We have audited the accompanying consolidated balance sheets of Sabine Oil & Gas Corporation and subsidiaries (the Company) as of December 31, 2014 and 2013, and the related consolidated statements of operations, shareholders (deficit) equity, and cash flows for each of the three years in the period ended December 31, 2014. These financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on the financial statements based on our audits.   We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reasonable assurance about whether the financial statements are free of material misstatement. The Company is not 

GPU Utilization:   0%|          | 0% , GPU0: 28%/6527MB | GPU1: 58%/9993MB


In [21]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

✅ Master ZIP created with flat structure: /kaggle/working/2014_DEEPSEEK_ALL_PARAPHRASED.zip


/kaggle/working/2014_DEEPSEEK_ALL_PARAPHRASED.zip

# 2016

In [12]:
year=2016

In [13]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['38984', '1580185', '786110', '1584701', '98222', '1058623', '920321', '1471261', '1499912', '1281922', '1382911', '1396279', '316300', '1040719', '1594590', '868725', '18172', '1403853', '1030749']
---------------------------
38984
----------------------------
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM  To the Board of Directors and Stockholders of  Real Industry, Inc.  We have audited the accompanying consolidated balance sheets of Real Industry, Inc. as of December 31, 2016 and 2015, and the related consolidated statements of operations, comprehensive income (loss), stockholders equity and cash flows for each of the two years in the period ended December 31, 2016. These financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those stand

In [14]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


Python garbage collector run.
CUDA cache emptied.
CUDA memory allocated after clearing: 0.00 GB
CUDA memory reserved after clearing: 0.00 GB
--------------------------------------------------
Ready to load a new model or continue with other operations.


In [15]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [16]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [17]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [18]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [19]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

In [20]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [21]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [22]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 0%/6101MB | GPU1: 0%/9429MB


📄 Processing CIK: 38984
----------------------------------------------



CIK NUMBER: 38984



Original AUDIT OPTINION: 
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM  To the Board of Directors and Stockholders of  Real Industry, Inc.  We have audited the accompanying consolidated balance sheets of Real Industry, Inc. as of December 31, 2016 and 2015, and the related consolidated statements of operations, comprehensive income (loss), stockholders equity and cash flows for each of the two years in the period ended December 31, 2016. These financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reasonable assurance about whether the financial statements are free of material mi

GPU Utilization:   0%|          | 0% , GPU0: 0%/6265MB | GPU1: 0%/9607MB

GPU Utilization:   0%|          | 0% , GPU0: 38%/6265MB | GPU1: 59%/9607MB

GPU Utilization:   0%|          | 0% , GPU0: 33%/6265MB | GPU1: 64%/9607MB

...

GPU Utilization:   0%|          | 0% , GPU0: 38%/7023MB | GPU1: 59%/10453MB

GPU Utilization:   0%|          | 0% , GPU0: 39%/7023MB | GPU1: 60%/10453MB

GPU Utilization:   0%|          | 0% , GPU0: 39%/7023MB | GPU1: 59%/10453MB

--- RAW LLM Output for Attempt 6 ---
Report of Independent Registered Public Accounting Firm        The Board of Directors and Stockholders  GulfMark Offshore, Inc.:     We have audited the accompanying consolidated balance sheets of GulfMark Offshore, Inc. and consolidated subsidiaries (the Company) as of December 31, 2016 and 2015, and the related consolidated statements of operations, comprehensive income (loss), stockholders equity, and cash flows for each of the years in the three-year period ended December 31, 2016. These consolidated financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on these consolidated financial statements based on our audits.     We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reasonable assurance about whether the financial statements are free of mat

GPU Utilization:   0%|          | 0% , GPU0: 39%/7023MB | GPU1: 59%/10453MB


In [24]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

✅ Master ZIP created with flat structure: /kaggle/working/2016_DEEPSEEK_ALL_PARAPHRASED.zip


/kaggle/working/2016_DEEPSEEK_ALL_PARAPHRASED.zip

# 2018

In [10]:
year=2018

In [11]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['1282648', '1528837', '2034', '1573166', '1584952', '1735828', '1547638', '708819', '931336', '1603923', '1056386', '1575360', '1056087', '1310067', '1690769', '1441849', '1405073', '1045425', '1461993']
---------------------------
1282648
----------------------------
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM   To the Board of Directors and Stockholders of  Halcón Resources Corporation  Houston, Texas  Opinion on the Financial Statements   We have audited the accompanying consolidated balance sheets of Halcón Resources Corporation and subsidiaries (the "Company") as of December 31, 2018 and 2017 (Successor Company Balance Sheet), the related consolidated statements of operations, shareholders' equity, and cash flows for the year ended December 31, 2018, 2017 and for the period from September 10, 2016 to December 31, 2016 (Successor Company operations) and January 1, 2016 to September 9, 2016 (Predecessor Company operations) and the related notes (collectively referred to

In [12]:
if 'model' in locals() and model is not None:
    del model
    print("DeepSeek model object deleted.")
if 'tokenizer' in locals() and tokenizer is not None:
    del tokenizer
    print("DeepSeek tokenizer object deleted.")

# 2. Explicitly run Python's garbage collector
#    This forces Python to reclaim memory from deleted objects.
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
#    This is crucial for freeing up unused GPU memory that PyTorch might have reserved.
torch.cuda.empty_cache()
print("CUDA cache emptied.")

# Optional: Print current GPU memory usage to verify
print(f"CUDA memory allocated after clearing: {torch.cuda.memory_allocated() / (1024**3):.2f} GB")
print(f"CUDA memory reserved after clearing: {torch.cuda.memory_reserved() / (1024**3):.2f} GB")

print("-" * 50)
print("Ready to load a new model or continue with other operations.")


Python garbage collector run.
CUDA cache emptied.
CUDA memory allocated after clearing: 0.00 GB
CUDA memory reserved after clearing: 0.00 GB
--------------------------------------------------
Ready to load a new model or continue with other operations.


In [13]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [14]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [15]:
device_map_balanced = {
    'model.embed_tokens': 0,
    'model.layers.0': 0,
    'model.layers.1': 0,
    'model.layers.2': 0,
    'model.layers.3': 0,
    'model.layers.4': 0,
    'model.layers.5': 0,
    'model.layers.6': 0,
    'model.layers.7': 0,
    'model.layers.8': 0,
    'model.layers.9': 0,
    'model.layers.10': 0,
    'model.layers.11': 0,
    'model.layers.12': 1,
    'model.layers.13': 1,
    'model.layers.14': 1,
    'model.layers.15': 1,
    'model.layers.16': 1,
    'model.layers.17': 1,
    'model.layers.18': 1,
    'model.layers.19': 1,
    'model.layers.20': 1,
    'model.layers.21': 1,
    'model.layers.22': 1,
    'model.layers.23': 1,
    'model.layers.24': 1,
    'model.layers.25': 1,
    'model.layers.26': 1,
    'model.layers.27.self_attn.q_proj': 1,
    'model.layers.27.self_attn.k_proj': 1,
    'model.layers.27.self_attn.v_proj': 1,
    'model.layers.27.self_attn.o_proj': 1,
    'model.layers.27.mlp': 1,
    'model.layers.27.input_layernorm': 1,
    'model.layers.27.post_attention_layernorm': 1,
    'model.layers.28': 1,
    'model.layers.29': 1,
    'model.layers.30': 1,
    'model.layers.31': 1,
    'model.norm': 1,
    'model.rotary_emb': 1,
    'lm_head': 1,
}

In [16]:
model_name = "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"

# Step 1: Load config
config = AutoConfig.from_pretrained(model_name)

# Step 2: Initialize empty model to infer device map or just override

with init_empty_weights():
    model = AutoModelForCausalLM.from_config(config)

# Instead of auto device map, use your corrected map
device_map = device_map_balanced

# Step 3: Load pretrained weights with device_map
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True
)

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [17]:
# Load the tokenizer for the DeepSeek model
tokenizer = AutoTokenizer.from_pretrained("deepseek-ai/DeepSeek-R1-Distill-Llama-8B")

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

In [18]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [19]:
def paraphrase_batch_deepseek(text, seeds, temps,token_count_input):
    text+=paraphrase_instruction
    results = []
    print (f"token of output paraphrased text must be more than: {token_count_input}")
     # embedding layer is on cuda:0
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        start_time = time.time()
        print ("Start of attempt : "+str(i+1))
        torch.manual_seed(seed)
         # Tokenize inputs and move to correct device
        inputs = tokenizer(text, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}
        outputs = model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,  # Buffer
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.pad_token_id
        )

        decoded = tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")



        final_paraphrase_matches = list(re.finditer(r"Final Paraphrased:", decoded))
    
        # Find all occurrences of "</think>"
        think_matches = list(re.finditer(r"</think>", decoded))
    
        extracted_part = None

        if len(final_paraphrase_matches) >= 2:
            start_index = final_paraphrase_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
        else:
            # Rule 2: If "Final Paraphrase:" appears only once, start from the last </think>
            # Find the *last* </think> that occurs
            start_index = think_matches[-1].end()
            match = re.search(r"(.*?)(?=\^|$)", decoded[start_index:], re.DOTALL)


            if match:
                extracted_part = match.group(1).strip()
    
    

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print("\n\n")
        print(extracted_part)
        print("\n\n")
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1} {model_small} ---\n")
        print("\n\n")
        print(f"Attempt {i + 1} took {time.time() - start_time:.2f} seconds\n\n")
        results.append(extracted_part)

    return results


In [20]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_deepseek(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 1%/6117MB | GPU1: 0%/9429MB


📄 Processing CIK: 1282648
----------------------------------------------



CIK NUMBER: 1282648



Original AUDIT OPTINION: 
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM   To the Board of Directors and Stockholders of  Halcón Resources Corporation  Houston, Texas  Opinion on the Financial Statements   We have audited the accompanying consolidated balance sheets of Halcón Resources Corporation and subsidiaries (the "Company") as of December 31, 2018 and 2017 (Successor Company Balance Sheet), the related consolidated statements of operations, shareholders' equity, and cash flows for the year ended December 31, 2018, 2017 and for the period from September 10, 2016 to December 31, 2016 (Successor Company operations) and January 1, 2016 to September 9, 2016 (Predecessor Company operations) and the related notes (collectively referred to as the "financial statements"). In our opinion, the Successor Company's financial statements present fairly, in all material respects, the fina

GPU Utilization:   0%|          | 0% , GPU0: 30%/6345MB | GPU1: 32%/9699MB

GPU Utilization:   0%|          | 0% , GPU0: 34%/6345MB | GPU1: 66%/9699MB

GPU Utilization:   0%|          | 0% , GPU0: 31%/6345MB | GPU1: 66%/9699MB

...

GPU Utilization:   0%|          | 0% , GPU0: 35%/6687MB | GPU1: 63%/10091MB

GPU Utilization:   0%|          | 0% , GPU0: 40%/6687MB | GPU1: 64%/10091MB

GPU Utilization:   0%|          | 0% , GPU0: 35%/6687MB | GPU1: 58%/10091MB

--- RAW LLM Output for Attempt 6 ---
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM  To the shareholders and the Board of Directors of Melinta Therapeutics, Inc.  Opinions on the Financial Statements and Internal Control over Financial Reporting  We have audited the accompanying consolidated balance sheets of Melinta Therapeutics, Inc. and subsidiaries (the "Company") as of December 31, 2018 and 2017, the related consolidated statements of operations, shareholders' equity, and cash flows, for each of the three years in the period ended December 31, 2018, and the related notes (collectively referred to as the "financial statements"). We also have audited the Companys internal control over financial reporting as of December 31, 2018, based on criteria established in Internal Control - Integrated Framework (2013) issued by the Committee of Sponsoring Organizations of the Treadway Commission (COSO).  In our opinion, the financial statements referred to above present fairly, in al

GPU Utilization:   0%|          | 0% , GPU0: 35%/6687MB | GPU1: 58%/10091MB


In [22]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

✅ Master ZIP created with flat structure: /kaggle/working/2018_DEEPSEEK_ALL_PARAPHRASED.zip


/kaggle/working/2018_DEEPSEEK_ALL_PARAPHRASED.zip